Install a recent version of requests for streaming support

In [ ]:
!pip install requests==2.25.1

In [ ]:
import requests
import shutil
import os
import sys
import importlib

In [ ]:
install_prefix = "/dli/task"
data_directory = os.path.join(install_prefix, 'data')
binary_prefix = os.path.join(install_prefix, 'kalman_binary')

Some useful functions

In [ ]:
def download_file(url, local_filename=None):
    if local_filename is None:
        local_filename = url.split('/')[-1]
    with requests.get(url, stream=True) as r:
        with open(local_filename, 'wb') as f:
            shutil.copyfileobj(r.raw, f)

    return local_filename

In [ ]:
def download_data():
    pwd = os.path.realpath('.')
    !mkdir -p $data_directory
    os.chdir(data_directory)
    if not os.path.exists(os.path.join(data_directory, 'hits.tar.gz')):
        download_file('https://surfdrive.surf.nl/files/index.php/s/6m5GQgtN6gHcd90/download', 'hits.tar.gz')
        download_file('https://surfdrive.surf.nl/files/index.php/s/RBNtGx5oNUpESnO/download', 'tracks.tar.gz')
        !tar zxf hits.tar.gz
        !tar zxf tracks.tar.gz
    os.chdir(pwd)

In [ ]:
def build(clean=False):
    """ 
    Some hacky stuff to build the module and then import it successfully
    """
    python_version = '{}.{}'.format(sys.version_info.major, sys.version_info.minor)
    package_dir = os.path.join('/usr/local/bin/miniconda', 'lib', 'python' + python_version, 'site-packages')
    if 'PYTHONPATH' not in os.environ:
        os.environ['PYTHONPATH'] =  package_dir        
    elif os.environ['PYTHONPATH'].find(package_dir) == -1:
        os.environ['PYTHONPATH'] = os.environ['PYTHONPATH'] + ':' + package_dir
    pwd = os.path.realpath('.')
    os.chdir(os.path.join(install_prefix, 'kalman_filter'))
    if clean:
        !python setup.py clean
    !python setup.py install
    os.chdir(pwd)
    import site
    try:
        importlib.reload(site)
    except NameError as e:
        pass

In [ ]:
def build_binary():
    pwd = os.path.realpath('.')
    build_dir = os.path.join(install_prefix, 'kalman_filter', 'build')
    !mkdir -p $build_dir
    os.chdir(build_dir)
    !cmake -Wno-dev -DCMAKE_INSTALL_PREFIX=$binary_prefix ..
    !make install
    os.chdir(pwd)

Download and install a recent CMake version

In [ ]:
def install_cmake():
    %cd /
    if not os.path.exists("/cmake.tar.gz"):
        download_file("https://github.com/Kitware/CMake/releases/download/v3.20.1/cmake-3.20.1-linux-x86_64.tar.gz", "/cmake.tar.gz")
        !tar zxf cmake.tar.gz
        !mv cmake-3.20.1-linux-x86_64 cmake
    os.environ['PATH'] = "/cmake/bin:" + os.environ['PATH']

In [ ]:
install_cmake()

Install git and clone the exercise git repository

In [ ]:
%cd $install_prefix
!apt update
!apt -y install git
!git clone https://gitlab.nikhef.nl/roelaaij/kalman_filter.git
!pip install pybind11 numpy

Download the input data

In [ ]:
download_data()

Build the exercise

In [ ]:
build()

Import the module and call the "run" function. 

Arguments:
- part (string): one of ["start", "SoA", "pinned_host_memory", "streams"]
- number of events (int)
- data location (string): '/dli/data/kf'
- number of repetitions
- device ID (int): leave at 0
- number of CUDA streams: only has an effect in the "streams" part of the exercise

In [ ]:
import kalman_filter

In [ ]:
kalman_filter.run('start', 10, data_directory, 10, 0, 0)

Also build an executable that can be used with the profiler

In [ ]:
build_binary()

Run the profiler to get an idea what part is taking time, the arguments are the same as above

In [ ]:
!nvprof $binary_prefix/bin/KalmanFilter start 10 $data_directory 10 0 0